<a href="https://colab.research.google.com/github/Requenamar3/Data-Mining/blob/main/Data%20Mining%20Module%205.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Running the Apriori Algorithm and Finding Association Rules in Online Retail Datasets


**Apply the Apriori algorithm and association rule mining to areal-world dataset**

##EDA

In [1]:
!pip install mlxtend -qqq

In [2]:
 # installing the pandas_profiling package for data analysis and generating statistical report summaries.
!pip install ydata_profiling


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 357.9/357.9 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 104.8/104.8 kB 9.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 686.1/686.1 kB 9.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 293.3/293.3 kB 9.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 296.5/296.5 kB 11.4 MB/s eta 0:00:00
  Created wheel for htmlmin: filename=htmlmin-0.1.12-py3-none-any.whl size=27080 sha256=f16f4d409854f2e7b5f1a477434cd693f9e0871486be13c2e95294ec8723ee09
  Stored in directory: /root/.cache/pip/wheels/dd/91/29/a79cecb328d01739e64017b6fb9a1ab9d8cb1853098ec5966d
Successfully built htmlmin
  Attempting uninstall: seaborn
    Found existing installation: seaborn 0.13.1
    Uninstalling seaborn-0.13.1:
      Successfully uninstalled seaborn-0.13.1


In [3]:
import pandas as pd
import matplotlib.pyplot as plt
import mlxtend.frequent_patterns
import mlxtend.preprocessing
import numpy
import datetime as dt
!pip install matplotlib


**check out the columns in the dataset in order to determine what columns to load**

In [4]:
base_url = 'https://raw.githubusercontent.com/Requenamar3/Data-Mining/main/'

# List of CSV file paths on GitHub
file_paths = [
    'sales_2023-01-01_2023-04-30.csv',
    'sales_2023-05-01_2023-09-30.csv',
    'sales_2024-03-07_2024-04-01.csv',
    'sales_2023-10-01_2024-03-06.csv',
]

# Function to get columns from a single CSV file
def get_columns_from_csv(file_path):
    full_url = f'{base_url}{file_path}'
    # Read just the first row to get the columns
    df = pd.read_csv(full_url, nrows=1)
    return df.columns.tolist()

# Check columns in each dataset
all_columns = set()
for file_path in file_paths:
    columns = get_columns_from_csv(file_path)
    all_columns.update(columns)

# print all_columns and decide which ones to load
print(all_columns)


/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


{'units_per_transaction', 'shipping_region', 'customer_email', 'customer_type', 'financial_status', 'order_name', 'variant_sku', 'net_sales', 'total_sales', 'customer_cohort_quarter', 'customer_id', 'product_title', 'day', 'customer_cohort_week', 'shipping_postal_code', 'total_cost', 'product_type', 'month', 'product_price', 'customer_cohort_month'}


**load only the columns needed**

In [5]:
import pandas as pd

base_url = 'https://raw.githubusercontent.com/Requenamar3/Data-Mining/main/'
file_paths = [
    'sales_2023-01-01_2023-04-30.csv',
    'sales_2023-05-01_2023-09-30.csv',
    'sales_2024-03-07_2024-04-01.csv',
    'sales_2023-10-01_2024-03-06.csv',
]

columns_to_load = [
    'total_sales', 'customer_type', 'product_title', 'customer_cohort_month',
    'order_name', 'month', 'shipping_postal_code', 'units_per_transaction',
    'product_price', 'shipping_region', 'total_cost', 'variant_sku',
    'net_sales', 'customer_id', 'financial_status'
]

dataframes_list = []

for file_path in file_paths:
    full_url = f'{base_url}{file_path}'
    # First, check which columns exist in the CSV
    available_columns = pd.read_csv(full_url, nrows=0).columns.tolist()
    # Determine the intersection of available columns and columns to load
    columns_to_read = [column for column in columns_to_load if column in available_columns]
    df = pd.read_csv(full_url, usecols=columns_to_read)
    dataframes_list.append(df)

BBORDERS = pd.concat(dataframes_list, ignore_index=True)
BBORDERS.head()


/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


month    financial_status order_name    customer_id customer_type  \
0  2023-01  partially_refunded    #658025  5213564469363     Returning   
1  2023-01            refunded    #667324  5922255994995     Returning   
2  2023-01            refunded    #667324  5922255994995     Returning   
3  2023-01            refunded    #655100  5446435405939     Returning   
4  2023-01            refunded    #655100  5446435405939     Returning   

  variant_sku  product_price                           product_title  \
0   SQ1726938         287.93                          Bloomsy Deluxe   
1         NaN           0.00                                     NaN   
2   SQ9178530         269.94                        Bloomsy Original   
3   SQ8862610         559.99  Bloomsy Premium BFCM 12 Months Prepaid   
4         NaN           0.00                                     NaN   

  shipping_region shipping_postal_code customer_cohort_month  total_sales  \
0           Texas                75204               2021-07       314.57   
1         Florida                34109               2022-07        41.94   
2         Florida                34109               2022-07       288.84   
3         Indiana                47012               2021-12         0.00   
4         Indiana                47012               2021-12         0.00   

   net_sales  total_cost  units_per_transaction  
0     287.93         0.0                      1  
1       0.00         0.0                      0  
2     269.94         0.0                      1  
3       0.00         0.0                      0  
4       0.00         0.0                      0

In [6]:
BBORDERS.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 473654 entries, 0 to 473653
Data columns (total 15 columns):
 #   Column                 Non-Null Count   Dtype  
---  ------                 --------------   -----  
 0   month                  450103 non-null  object 
 1   financial_status       473654 non-null  object 
 2   order_name             473654 non-null  object 
 3   customer_id            473654 non-null  int64  
 4   customer_type          473642 non-null  object 
 5   variant_sku            241781 non-null  object 
 6   product_price          473654 non-null  float64
 7   product_title          241798 non-null  object 
 8   shipping_region        473653 non-null  object 
 9   shipping_postal_code   473639 non-null  object 
 10  customer_cohort_month  473654 non-null  object 
 11  total_sales            473654 non-null  float64
 12  net_sales              473654 non-null  float64
 13  total_cost             473654 non-null  float64
 14  units_per_transaction  473654 non-nu

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [7]:
#Import the ProfileReport .For creating comprehensive exploratory data analysis reports.
from ydata_profiling import ProfileReport

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [8]:
# Create a ProfileReport object
profile = ProfileReport(BBORDERS, title="Shopify", explorative=True)


/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [9]:
# display report
profile

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

**create a unique Identifier by merging VariantSku and Ordername**

**run the profiler to find duplicates and missing values**

##Part 1: Running the Apriori Algorithm on the Complete Online Retail Dataset

### 1.Run the Apriori Algorithm: Apply the Apriori algorithm to the full dataset. Set parameters to identify item sets appearing in at least 1% of transactions.


### 2.Analysis of Specific Item Set: Filter to the item set containing "10 COLOUR SPACEBOY PEN." Analyze its support value.

### 3.Item Set Length Analysis: Add a column for item set length. Focus on sets of length two with support between 0.02 and 0.021. Compare these to previous results.

### 4.Support Value Distribution: Plot the distribution of support values for the identified item sets

##Part 2: Finding the Association Rules on the Complete Online Retail Dataset

### 1.Fit Association Rule Model: Use the full dataset to generate association rules. Apply the confidence metric with a minimum threshold of 0.6.

### 2.Count and Compare Association Rules: Count the number of derived rules. Compare this with previous exercises.

### 3.Plot Confidence vs. Support: Create a plot to visualize the relationship between confidence and support for the rules.

### 4.Analyze Rule Metrics: Examine the distributions of confidence, lift, leverage, and conviction in your rules.

##Report writing



*   Insights gained from the Apriori algorithm and association rule mining.
*   How these insights can influence business decisions like store layout and pricing.

*   A comparison between the two datasets.
*   Reflections on how data partitioning and increasing data volume impact results.



